Import the latest data directly from the berlin website

In [1]:
import pandas as pd
pd.set_option('display.max_columns', None)

url_berlin='https://www.berlin.de/lageso/gesundheit/infektionskrankheiten/corona/tabelle-bezirke-gesamtuebersicht/'

data=pd.read_html(url_berlin)[0]

data.Datum=pd.to_datetime(data.Datum,format="%d.%m.%Y")
data=data[::-1]
bezirks=['Mitte', 'Friedrichshain-Kreuzberg', 'Pankow',
       'Charlottenburg-Wilmersdorf', 'Spandau', 'Steglitz-Zehlendorf',
       'Tempelhof-Schöneberg', 'Neukölln', 'Treptow-Köpenick',
       'Marzahn-Hellersdorf', 'Lichtenberg', 'Reinickendorf']
#rename each bezirk to its full name (important for later when we use geoplots!)
data=data.rename(columns={'MI':'Mitte', 'FK':'Friedrichshain-Kreuzberg', 
                          'PA':'Pankow', 'CW':'Charlottenburg-Wilmersdorf',
                          'SP':'Spandau', 'SZ':'Steglitz-Zehlendorf', 
                          'TS':'Tempelhof-Schöneberg', 'NK':'Neukölln', 
                          'TK':'Treptow-Köpenick', 'MH':'Marzahn-Hellersdorf',
                          'LI':'Lichtenberg', 'RD':'Reinickendorf'})
#add a column for the total cases:
data['All_berlin']=data[bezirks].mean(axis=1)
#transform it for each bezirk into the 7day inzidenz
for bezirk in bezirks:
    data[bezirk+'_7dI']=data[bezirk].rolling(window=7).mean()
data['All_berlin_7dI']=data['All_berlin'].rolling(window=7).mean()

load the district outlines. The file bezirksgrenzen.geojson can be downloaded from https://daten.odis-berlin.de/de/dataset/bezirksgrenzen/

In [3]:
#Loading the geoapandas bezirksgrenzen
from geojson_rewind import rewind
import geopandas as gpd

bezirksgrenzen_f=gpd.read_file('bezirksgrenzen.geojson')
bezirksgrenzen=bezirksgrenzen_f[["Gemeinde_name", "geometry"]].set_index("Gemeinde_name")

#need to reverse some bezirks, otherwise the plotting looks weird
bezirks_to_reverse=['Spandau','Steglitz-Zehlendorf','Treptow-Köpenick','Reinickendorf','Pankow']
from shapely.geometry import polygon
from shapely.geometry import MultiPolygon
for bez in bezirks_to_reverse:
    ex=bezirksgrenzen.loc[bez][0]
    
    ex_poly_rev=polygon.orient(ex[0],-1)

    ex=MultiPolygon([polygon.orient(ex[i],-1) for i in range(len(ex))])
    #print(ex)
    bezirksgrenzen.loc[bez]=ex

Reshape the dataframe with the Covid incidence data

In [4]:
bezirks=['Mitte', 'Friedrichshain-Kreuzberg', 'Pankow',
       'Charlottenburg-Wilmersdorf', 'Spandau', 'Steglitz-Zehlendorf',
       'Tempelhof-Schöneberg', 'Neukölln', 'Treptow-Köpenick',
       'Marzahn-Hellersdorf', 'Lichtenberg', 'Reinickendorf']

df=pd.DataFrame({'Bezirk':[bezirks[0]]*(len(data.Datum)-1),'Datum':data.Datum[1:],'7dI':data[bezirks[0]+'_7dI'][1:]})
for bezirk in bezirks[1:]:
    df2=pd.DataFrame({'Bezirk':[bezirk]*(len(data.Datum)-1),'Datum':data.Datum[1:],'7dI':data[bezirk+'_7dI'][1:]})
    df=pd.concat([df,df2],ignore_index=True)

#print(df.head(10))
df.Datum=df.Datum.apply(lambda x: x.strftime('%Y-%m-%d'))
#print(df.dtypes)

#print(df.Datum.unique())
dates=df.Datum.unique()

Make and save all the figures

In [5]:
from plotly.subplots import make_subplots
import plotly.graph_objects as go
import json
import numpy as np

import os
if not os.path.exists("images_covid19_berlin"):
    os.mkdir("images_covid19_berlin")

template='plotly_dark'

poly_json=json.loads(bezirksgrenzen.to_json())

for date in dates[8:]:
    print(date)
    df2=df[df.Datum==date]
    fig=make_subplots(rows=2,cols=1,
                     specs=[[{'type':'scatter'}],[{'type':'choropleth'}]],
                     vertical_spacing=0.05, horizontal_spacing=0.)
    fig.add_trace(go.Choropleth(
        geojson=poly_json,
        colorscale='matter_r',
        locations=df2['Bezirk'].astype(str),
        z=df2['7dI'],
        locationmode='geojson-id',
        zmin=0,zmax=df['7dI'].max(),
        colorbar_title='7dI'
    ),row=2,col=1)
    fig.update_geos(fitbounds="locations",visible=False)
    fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0},
                     template=template)
                    #plot_bgcolor='rgba(0,0,0,0)')
    #add the trace of the total 
    fig.add_trace(go.Line(x=data.Datum,y=data['All_berlin_7dI']),
                 row=1,col=1)
    fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0})#,template=template),
                     #paper_bgcolor='rgba(0,0,0,0)')

    fig.update_layout(shapes=[
        dict(
          type= 'line',
          yref= 'y', y0= 0, y1= 100,
          xref= 'x', x0= date, x1= date
        )
    ])
    fig.update_layout(yaxis2=dict(showgrid=False))
    fig['layout']['yaxis']['title']='Berlin total 7 day Incidence'
    fig.write_image('images_covid19_berlin/'+date+'.png')
    #fig.show()

2020-03-11


C:\Users\Anja\Desktop\new try\WPy64-3770\python-3.7.7.amd64\lib\site-packages\plotly\graph_objs\_deprecations.py:385: DeprecationWarning:

plotly.graph_objs.Line is deprecated.
Please replace it with one of the following more specific types
  - plotly.graph_objs.scatter.Line
  - plotly.graph_objs.layout.shape.Line
  - etc.




In [7]:
#now make a gif out of it!
import imageio
images = []
for filename in [('images_covid19_berlin/'+date+'.png') for date in dates[8:]:
    images.append(imageio.imread(filename))
imageio.mimsave('images_covid19_berlin/berlin.gif', images,duration=0.05)